In [1]:
from numpy import load
from numpy import zeros
from numpy import ones
from numpy.random import randint
from numpy.random import choice
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.initializers import RandomNormal
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input
from tensorflow.keras.layers import Conv2D
from tensorflow.keras.layers import Conv2DTranspose
from tensorflow.keras.layers import LeakyReLU
from tensorflow.keras.layers import Activation
from tensorflow.keras.layers import Concatenate
from tensorflow.keras.layers import Dropout
from tensorflow.keras.layers import BatchNormalization
from tensorflow.keras.layers import LeakyReLU
from tensorflow.keras.models import load_model
import matplotlib.pyplot as plt
import h5py

In [2]:
# define the discriminator model
def define_discriminator(image_shape):
    # weight initialization
    init = RandomNormal(stddev=0.02)
    # source image input
    in_src_image = Input(shape=image_shape)
    # target image input
    in_target_image = Input(shape=image_shape)
    # concatenate images channel-wise
    merged = Concatenate()([in_src_image, in_target_image])
    # C64
    d = Conv2D(64, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(merged)
    d = LeakyReLU(alpha=0.2)(d)
    # C128
    d = Conv2D(128, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(d)
    d = BatchNormalization()(d)
    d = LeakyReLU(alpha=0.2)(d)
    # C256
    d = Conv2D(256, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(d)
    d = BatchNormalization()(d)
    d = LeakyReLU(alpha=0.2)(d)
    # C512
    d = Conv2D(512, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(d)
    d = BatchNormalization()(d)
    d = LeakyReLU(alpha=0.2)(d)
    # second last output layer
    d = Conv2D(512, (4,4), padding='same', kernel_initializer=init)(d)
    d = BatchNormalization()(d)
    d = LeakyReLU(alpha=0.2)(d)
    # patch output
    d = Conv2D(1, (4,4), padding='same', kernel_initializer=init)(d)
    patch_out = Activation('sigmoid')(d)
    # define model
    model = Model([in_src_image, in_target_image], patch_out)
    # compile model
    opt = Adam(lr=0.0002, beta_1=0.5)
    model.compile(loss='binary_crossentropy',optimizer=opt, loss_weights=[0.5])
    #model.summary()
    return model

In [3]:
# define an encoder block
def define_encoder_block(layer_in, n_filters, batchnorm=True):
    # weight initialization
    init = RandomNormal(stddev=0.02)
    # add downsampling layer
    g = Conv2D(n_filters, (4,4), strides=(2,2), padding='same',kernel_initializer=init)(layer_in)

    # conditionally add batch normalization
    if batchnorm:
        g = BatchNormalization()(g, training=True)
    # leaky relu activation
    g = LeakyReLU(alpha = 0.2)(g)
    return g

In [4]:
# define a decorder block
def decoder_block(layer_in, skip_in, n_filters, dropout=True):
    # weight initialization
    init = RandomNormal(stddev=0.02)
    # add upsampling layer
    g = Conv2DTranspose(n_filters, (4,4), strides=(2,2), padding='same',kernel_initializer=init)(layer_in)
    # add batch normalization
    g = BatchNormalization()(g, training=True)
    # conditionally add dropout
    if dropout:
        g = Dropout(0.5)(g, training=True)
    # merge with skip connection
    g = Concatenate()([g, skip_in])
    # relu activation
    g = Activation('relu')(g)
    return g

In [5]:
# define the standalone generator model
def define_generator(image_shape=(256, 256, 3)):
    # weight initialization
    init = RandomNormal(stddev=0.02)
    # image input
    in_image = Input(shape=image_shape)
    # encoder model
    e1 = define_encoder_block(in_image, 64, batchnorm = False)
    e2 = define_encoder_block(e1, 128)
    e3 = define_encoder_block(e2, 256)
    e4 = define_encoder_block(e3, 512)
    e5 = define_encoder_block(e4, 512)
    e6 = define_encoder_block(e5, 512)
    e7 = define_encoder_block(e6, 512)
    # bottleneck, no batch norm and relu
    b = Conv2D(512, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(e7)
    b = Activation('relu')(b)
    # decoder model
    d1 = decoder_block(b, e7, 512)
    d2 = decoder_block(d1, e6, 512)
    d3 = decoder_block(d2, e5, 512)
    d4 = decoder_block(d3, e4, 512, dropout=False)
    d5 = decoder_block(d4, e3, 256, dropout=False)
    d6 = decoder_block(d5, e2, 128, dropout=False)
    d7 = decoder_block(d6, e1, 64, dropout=False)
    # output
    g = Conv2DTranspose(3, (4,4), strides=(2,2), padding='same', kernel_initializer=init)(d7)
    out_image = Activation('tanh')(g)
    # define model
    model = Model(in_image, out_image)
    #model.summary()
    return model

In [6]:
# define the combined generator and discriminator model, for updaing the generator
def define_gan(g_model, d_model, image_shape):
    # make weights in the discriminator not trainable
    d_model.trainable = False
    # define the source image
    in_src = Input(shape=image_shape)
    # connect the source image to the generator input
    gen_out = g_model(in_src)
    # connect the source input and generator output to the discriminator input
    dis_out = d_model([in_src, gen_out])
    # src image as input, generated image and classification output
    model = Model(in_src, [dis_out, gen_out])
    # compile model
    opt = Adam(lr=0.0002, beta_1=0.5)
    model.compile(loss=['binary_crossentropy', 'mae'], optimizer=opt, loss_weights=[1,100])
    return model

In [7]:
# load and prepare training images
def load_real_samples(filename):
    f = h5py.File(filename, 'r')
    # unpack the arrays
    X1 = f['sketches']
    X2 = f['heightmaps']
    # scale from [0,255] to [-1, 1]
    #X1 = (X1[:]-127.5) / 127.5
    #X2 = (X2[:]-127.5) / 127.5

    return [X1, X2]

In [8]:
# select a batch of random samples, returns images and target
def generate_real_samples(datasetA, datasetB, n_samples, patch_shape): #data 1 32 #2

    # choose random instances
    ix = range(datasetA.shape[0])
    
    # choose n_samples of integers at random without replacement
    # sort the result
    ix = sorted(choice(ix, size=n_samples, replace=False))
    
    # retrieve selected images
    X1, X2 = datasetA[ix], datasetB[ix]
    
    # generate 'real' class labels (1)
    y = ones((n_samples, patch_shape, patch_shape, 1))
    
    return [X1, X2], y

In [9]:
# generate a batch of images, returns images and targets
def generate_fake_samples(g_model, samples, patch_shape):
    # generate fake instance
    x = g_model.predict(samples)
    # create 'fake' class labels (0)
    y = zeros((len(x), patch_shape, patch_shape, 1))
    return x, y

In [10]:
# Training and preformance functions

# save summary of the model to disk
def summary2file(model, filename):
    with open(filename, 'w') as f:
        with redirect_stdout(f):
            model.summary()

In [11]:
# create and save a plot of generated images (reversed grayscale)
def save_plot(examples, epoch, n=5):
    # plot image
    for i in range(n * n):
        # define subplot
        plt.subplot(n, n, 1 + i)
        
        # turn off axis
        plt.axis('off')
        
        # plot raw pixel data
        plt.imshow(examples[i, :, :, 0], cmap='gray_r')
        
    # save plot to file
    filename = 'results/pix2pix_generated_plot_e%03d.png' % (epoch + 1)
    plt.savefig(filename)
    plt.close()

In [12]:
# plot history
def plot_history(d1_hist, d2_hist, g_hist, i):
    # plot loss
    plt.subplot(1, 1, 1)
    plt.plot(d1_hist, label='d-real')
    plt.xlabel('Batch Number')
    plt.ylabel('Loss')
    plt.title('D-Loss: Real')
    
    # plot layout
    plt.tight_layout()
    
    # save plot to file
    filename = 'results/pix2pix_plot_line_plot_loss1_%06d.png' % i
    plt.savefig(filename, dpi=300)
    plt.close()
    
    plt.subplot(1, 1, 1)
    plt.plot(d2_hist, label='d-fake')
    plt.xlabel('Batch Number')
    plt.ylabel('Loss')
    plt.title('G-Loss')
    
    # plot layout
    plt.tight_layout()
    
    # save plot to file
    filename = 'results/pix2pix_plot_line_plot_loss2_%06d.png' % i
    plt.savefig(filename, dpi=300)
    plt.close()
    
    plt.subplot(1, 1, 1)
    plt.plot(g_hist, label='gen')
    plt.xlabel('Batch Number')
    plt.ylabel('Loss')
    plt.title('G-Loss')
    
    # plot layout
    plt.tight_layout()
    
    # save plot to file
    filename = 'results/pix2pix_plot_line_plot_loss3_%06d.png' % i
    plt.savefig(filename, dpi=300)
    plt.close()

In [13]:
# generate samples and save as a plot and save the model
def summarize_performance(epoch, g_model, d_model, gan_model, datasetA, datasetB, n_samples=5):
    # select a sample of input images
    [X_realA, X_realB], _ = generate_real_samples(datasetA, datasetB, n_samples, 1)
    # generate a batch of fake samples
    X_fakeB, _ = generate_fake_samples(g_model, X_realA, 1)
    # scale all pixels from [-1,0] to [0,1]
    X_realA = (X_realA + 1) / 2.0
    X_realB = (X_realB + 1) / 2.0
    X_fakeB = (X_fakeB + 1) / 2.0
    # plot real source images
    for i in range(n_samples):
        plt.subplot(3, n_samples, 1 + i)
        plt.axis('off')
        plt.imshow(X_realA[i])
    # plot generated target image
    for i in range(n_samples):
        plt.subplot(3, n_samples, 1 + n_samples + i)
        plt.axis('off')
        plt.imshow(X_fakeB[i])
    # plot real target image
    for i in range(n_samples):
        plt.subplot(3, n_samples, 1 + n_samples*2 + i)
        plt.axis('off')
        plt.imshow(X_realB[i])
    # save plot to file
    filename1 = 'results/pix2pix_plot_%06d.png' % (epoch+1)
    plt.savefig(filename1, dpi=300)
    plt.close()
    # save the generator model
    filename2 = 'results/pix2pix_g_model_%06d.h5' % (epoch+1)
    g_model.save(filename2)
    
    filename3 = 'results/pix2pix_d_model_%06d.h5' % (epoch+1)
    d_model.save(filename3)
    
    filename4 = 'results/pix2pix_gan_model_%06d.h5' % (epoch+1)
    gan_model.save(filename4)
    print('>Saved: %s and %s' % (filename1, filename2))

In [14]:
def save_loss(d1_hist, d2_hist, g_hist, i):
    with open('results/d1_hist_%06d.txt' % (i+1), 'w') as f:
        for item in d1_hist:
            f.write("%s\n" % item)
            
    with open('results/d2_hist_%06d.txt' % (i+1), 'w') as f:
        for item in d2_hist:
            f.write("%s\n" % item)
            
    with open('results/g_hist_%06d.txt' % (i+1), 'w') as f:
        for item in g_hist:
            f.write("%s\n" % item)

In [15]:
# train pix2pix models
def train(d_model, g_model, gan_model, dataset, n_epochs=50, n_batch=15):
    
    # prepare lists for storing stats each iteration
    d1_hist, d2_hist, g_hist = list(), list(), list()
    
    # determine the output square shape of the discriminator
    n_patch = d_model.output_shape[1]
    # unpack dataset
    #trainA, trainB = dataset[0], dataset[1]
    
    trainA, trainB = load_real_samples('dataset.hdf5')
    
    # calculate the number of batches per training epoch
    #bat_per_epo = int(len(trainA) / n_batch)
    bat_per_epo = int(trainA.shape[0] / n_batch)
    
    
    # calculate the number of training iterations
    #n_steps = bat_per_epo * n_epochs
    

    # manually enumerate epochs
    for i in range(n_epochs):
        # enumerate batches over the training set
        for j in range(bat_per_epo):
            # select a batch of real samples
            [X_realA, X_realB], y_real = generate_real_samples(trainA, trainB, n_batch, n_patch)
            # generate a batch of fake samples
            X_fakeB, y_fake = generate_fake_samples(g_model, X_realA, n_patch)
            # update discriminator for real samples
            d_loss1 = d_model.train_on_batch([X_realA, X_realB], y_real)
            # update discriminator for generated samples
            d_loss2 = d_model.train_on_batch([X_realA, X_fakeB], y_fake)
            # update the generator
            g_loss, _, _ = gan_model.train_on_batch(X_realA, [y_real, X_realB])
            # summarize performance
            print('>%d/%d, %d/%d, d1[%.8f] d2[%.8f] g[%.8f]' % (i+46, n_epochs+50, j+1, bat_per_epo, d_loss1, d_loss2, g_loss))
            
            # record history
            d1_hist.append(d_loss1)
            d2_hist.append(d_loss2)
            g_hist.append(g_loss)
        
        # calculate the model performance every 10 epochs
        if(i+1) % 5 == 0:
            summarize_performance(i+45, g_model, d_model, gan_model, trainA, trainB)
            plot_history(d1_hist, d2_hist, g_hist, i+45)
            
        save_loss(d1_hist, d2_hist, g_hist, i+45)
        d1_hist, d2_hist, g_hist = list(), list(), list()
        
    # create history plot at the conclusion of training
    plot_history(d1_hist, d2_hist, g_hist, 1000)

In [16]:
# load image data
dataset = load_real_samples('dataset.hdf5')
print('Loaded', dataset[0].shape, dataset[1].shape)
# define input shape based on the loaded dataset
image_shape = dataset[0].shape[1:]
print(image_shape)
# define the models
#d_model = define_discriminator(image_shape)
#g_model = define_generator(image_shape)
# define the composite model
#gan_model = define_gan(g_model, d_model, image_shape)

d_model = load_model('results/pix2pix_d_model_000045.h5')
g_model = load_model('results/pix2pix_g_model_000045.h5')
gan_model = load_model('results/pix2pix_gan_model_000045.h5')

# train model
train(d_model, g_model, gan_model, dataset)


Loaded (21472, 256, 256, 3) (21472, 256, 256, 3)
(256, 256, 3)
>46/100, 1/1431, d1[0.00000095] d2[0.00000025] g[19.10878563]
>46/100, 2/1431, d1[0.00000111] d2[0.00000175] g[4.22380877]
>46/100, 3/1431, d1[0.00000150] d2[0.00000045] g[4.29424810]
>46/100, 4/1431, d1[0.00000083] d2[0.00000186] g[5.13677740]
>46/100, 5/1431, d1[0.00000271] d2[0.00000114] g[4.10128450]
>46/100, 6/1431, d1[0.00000143] d2[0.00000043] g[3.78456068]
>46/100, 7/1431, d1[0.00000094] d2[0.00000199] g[3.93677282]
>46/100, 8/1431, d1[0.00000337] d2[0.00000091] g[3.42863035]
>46/100, 9/1431, d1[0.00000084] d2[0.00000037] g[4.09754896]
>46/100, 10/1431, d1[0.00000069] d2[0.00000019] g[3.86360574]
>46/100, 11/1431, d1[0.00000043] d2[0.00000017] g[4.05888128]
>46/100, 12/1431, d1[0.00000097] d2[0.00000053] g[3.76022792]
>46/100, 13/1431, d1[0.00000290] d2[0.00000079] g[3.39524841]
>46/100, 14/1431, d1[0.00000092] d2[0.00000066] g[3.18842697]
>46/100, 15/1431, d1[0.00000093] d2[0.00000107] g[3.74331212]
>46/100, 16/143

>46/100, 126/1431, d1[0.00000061] d2[0.00000048] g[3.23165751]
>46/100, 127/1431, d1[0.00000195] d2[0.00000030] g[2.75539565]
>46/100, 128/1431, d1[0.00000175] d2[0.00000054] g[3.07083106]
>46/100, 129/1431, d1[0.00000313] d2[0.00000031] g[2.94084287]
>46/100, 130/1431, d1[0.00000191] d2[0.00000722] g[3.11234784]
>46/100, 131/1431, d1[0.00000100] d2[0.00000016] g[3.06353068]
>46/100, 132/1431, d1[0.00000051] d2[0.00000063] g[3.76218033]
>46/100, 133/1431, d1[0.00000139] d2[0.00000195] g[3.01845169]
>46/100, 134/1431, d1[0.00000070] d2[0.00000032] g[3.23871899]
>46/100, 135/1431, d1[0.00000056] d2[0.00000049] g[3.88512683]
>46/100, 136/1431, d1[0.00000077] d2[0.00000039] g[3.09466052]
>46/100, 137/1431, d1[0.00000124] d2[0.00000018] g[3.67540550]
>46/100, 138/1431, d1[0.00000222] d2[0.00000069] g[3.19274998]
>46/100, 139/1431, d1[0.00000057] d2[0.00000129] g[3.43295574]
>46/100, 140/1431, d1[0.00000112] d2[0.00001222] g[3.09361053]
>46/100, 141/1431, d1[0.00000235] d2[0.00000053] g[2.87

>46/100, 257/1431, d1[0.00000066] d2[0.00000034] g[3.37010026]
>46/100, 258/1431, d1[0.00000056] d2[0.00000033] g[3.09256244]
>46/100, 259/1431, d1[0.00000102] d2[0.00000175] g[3.28111124]
>46/100, 260/1431, d1[0.00000356] d2[0.00000047] g[2.75978303]
>46/100, 261/1431, d1[0.00000262] d2[0.00000044] g[3.13984942]
>46/100, 262/1431, d1[0.00000146] d2[0.00000078] g[3.31834841]
>46/100, 263/1431, d1[0.00000071] d2[0.00000036] g[3.21761227]
>46/100, 264/1431, d1[0.00000194] d2[0.00000020] g[2.97655392]
>46/100, 265/1431, d1[0.00000228] d2[0.00000073] g[2.79342890]
>46/100, 266/1431, d1[0.00000073] d2[0.00000129] g[3.55491400]
>46/100, 267/1431, d1[0.00000287] d2[0.00000072] g[2.84050488]
>46/100, 268/1431, d1[0.00000204] d2[0.00000159] g[3.25818300]
>46/100, 269/1431, d1[0.00000066] d2[0.00000048] g[3.21264505]
>46/100, 270/1431, d1[0.00000113] d2[0.00000008] g[3.11746979]
>46/100, 271/1431, d1[0.00000072] d2[0.00000048] g[3.48423433]
>46/100, 272/1431, d1[0.00000142] d2[0.00000055] g[3.41

>46/100, 388/1431, d1[0.00000034] d2[0.00000024] g[4.06096792]
>46/100, 389/1431, d1[0.00000318] d2[0.00000016] g[2.63074565]
>46/100, 390/1431, d1[0.00000060] d2[0.00000060] g[3.08607078]
>46/100, 391/1431, d1[0.00000202] d2[0.00000044] g[2.82681966]
>46/100, 392/1431, d1[0.00000163] d2[0.00000020] g[3.51690412]
>46/100, 393/1431, d1[0.00000053] d2[0.00000054] g[3.57757139]
>46/100, 394/1431, d1[0.00000064] d2[0.00000119] g[3.59072804]
>46/100, 395/1431, d1[0.00000051] d2[0.00000020] g[3.71566248]
>46/100, 396/1431, d1[0.00000156] d2[0.00000073] g[3.43413258]
>46/100, 397/1431, d1[0.00000086] d2[0.00000011] g[3.25555468]
>46/100, 398/1431, d1[0.00000126] d2[0.00000114] g[2.75358438]
>46/100, 399/1431, d1[0.00000111] d2[0.00000104] g[3.45801616]
>46/100, 400/1431, d1[0.00000094] d2[0.00000106] g[3.21353745]
>46/100, 401/1431, d1[0.00000045] d2[0.00000027] g[3.96256423]
>46/100, 402/1431, d1[0.00000172] d2[0.00000061] g[3.21342111]
>46/100, 403/1431, d1[0.00000136] d2[0.00000217] g[2.99

>46/100, 519/1431, d1[0.00000036] d2[0.00000078] g[3.84828353]
>46/100, 520/1431, d1[0.00000067] d2[0.00000165] g[3.27746391]
>46/100, 521/1431, d1[0.00000057] d2[0.00000032] g[3.15244222]
>46/100, 522/1431, d1[0.00000054] d2[0.00000022] g[3.12626505]
>46/100, 523/1431, d1[0.00000125] d2[0.00000026] g[3.14473295]
>46/100, 524/1431, d1[0.00000075] d2[0.00000082] g[3.55827141]
>46/100, 525/1431, d1[0.00000177] d2[0.00000105] g[2.86927938]
>46/100, 526/1431, d1[0.00000072] d2[0.00000138] g[3.62905526]
>46/100, 527/1431, d1[0.00000128] d2[0.00000082] g[2.78316641]
>46/100, 528/1431, d1[0.00000344] d2[0.00000144] g[2.57101226]
>46/100, 529/1431, d1[0.00000569] d2[0.00000015] g[2.68794203]
>46/100, 530/1431, d1[0.00000073] d2[0.00000032] g[3.54735494]
>46/100, 531/1431, d1[0.00000070] d2[0.00000065] g[3.13705945]
>46/100, 532/1431, d1[0.00000146] d2[0.00000017] g[3.19548059]
>46/100, 533/1431, d1[0.00000105] d2[0.00000074] g[2.92198706]
>46/100, 534/1431, d1[0.00002698] d2[0.00000044] g[2.55

...

>95/100, 821/1431, d1[0.00000142] d2[0.00000112] g[2.41035891]
>95/100, 822/1431, d1[0.00000055] d2[0.00000121] g[2.63705993]
>95/100, 823/1431, d1[0.00000077] d2[0.00000044] g[2.30385613]
>95/100, 824/1431, d1[0.00000051] d2[0.00000065] g[2.83808851]
>95/100, 825/1431, d1[0.00000035] d2[0.00000147] g[3.12297726]
>95/100, 826/1431, d1[0.00000157] d2[0.00000048] g[2.31457782]
>95/100, 827/1431, d1[0.00000058] d2[0.00000114] g[2.15525150]
>95/100, 828/1431, d1[0.00000160] d2[0.00000044] g[2.14459395]
>95/100, 829/1431, d1[0.00000052] d2[0.00000022] g[2.05475235]
>95/100, 830/1431, d1[0.00000156] d2[0.00000237] g[2.06203771]
>95/100, 831/1431, d1[0.00000146] d2[0.00000040] g[2.05177474]
>95/100, 832/1431, d1[0.00000033] d2[0.00000187] g[2.73861074]
>95/100, 833/1431, d1[0.00000095] d2[0.00000034] g[2.52001309]
>95/100, 834/1431, d1[0.00000078] d2[0.00000183] g[2.30728316]
>95/100, 835/1431, d1[0.00000155] d2[0.00000043] g[2.05156207]
>95/100, 836/1431, d1[0.00000085] d2[0.00000537] g[2.49

>95/100, 952/1431, d1[0.00000310] d2[0.00000224] g[2.06320882]
>95/100, 953/1431, d1[0.00000193] d2[0.00000210] g[2.01304555]
>95/100, 954/1431, d1[0.00000073] d2[0.00000177] g[2.30006766]
>95/100, 955/1431, d1[0.00000055] d2[0.00000070] g[2.46770525]
>95/100, 956/1431, d1[0.00000055] d2[0.00000086] g[2.48712444]
>95/100, 957/1431, d1[0.00000266] d2[0.00000021] g[2.04960704]
>95/100, 958/1431, d1[0.00000047] d2[0.00000039] g[2.58866477]
>95/100, 959/1431, d1[0.00000111] d2[0.00000048] g[1.99740946]
>95/100, 960/1431, d1[0.00000074] d2[0.00000083] g[2.21465707]
>95/100, 961/1431, d1[0.00000121] d2[0.00000043] g[1.96115732]
>95/100, 962/1431, d1[0.00000084] d2[0.00000073] g[2.32373381]
>95/100, 963/1431, d1[0.00000531] d2[0.00000038] g[1.81350565]
>95/100, 964/1431, d1[0.00000084] d2[0.00000083] g[2.31278419]
>95/100, 965/1431, d1[0.00000115] d2[0.00000045] g[2.36711383]
>95/100, 966/1431, d1[0.00000058] d2[0.00000061] g[2.58124065]
>95/100, 967/1431, d1[0.00000157] d2[0.00000082] g[2.09

>95/100, 1081/1431, d1[0.00000098] d2[0.00000068] g[2.06184697]
>95/100, 1082/1431, d1[0.00000095] d2[0.00000026] g[2.21421289]
>95/100, 1083/1431, d1[0.00000221] d2[0.00000043] g[2.16671634]
>95/100, 1084/1431, d1[0.00000072] d2[0.00000112] g[2.63905740]
>95/100, 1085/1431, d1[0.00000210] d2[0.00000077] g[1.84591091]
>95/100, 1086/1431, d1[0.00000051] d2[0.00000030] g[2.99312878]
>95/100, 1087/1431, d1[0.00000046] d2[0.00000057] g[2.46496248]
>95/100, 1088/1431, d1[0.00000086] d2[0.00000151] g[2.55181456]
>95/100, 1089/1431, d1[0.00001951] d2[0.00000138] g[1.92318881]
>95/100, 1090/1431, d1[0.00000041] d2[0.00000142] g[2.32733369]
>95/100, 1091/1431, d1[0.00000047] d2[0.00000086] g[2.34519148]
>95/100, 1092/1431, d1[0.00000088] d2[0.00000151] g[2.46382785]
>95/100, 1093/1431, d1[0.00000114] d2[0.00000043] g[2.11376786]
>95/100, 1094/1431, d1[0.00000035] d2[0.00000051] g[2.56298184]
>95/100, 1095/1431, d1[0.00000145] d2[0.00000182] g[2.20479703]
>95/100, 1096/1431, d1[0.00000079] d2[0.

>95/100, 1210/1431, d1[0.00000629] d2[0.00000406] g[2.16646528]
>95/100, 1211/1431, d1[0.00000061] d2[0.00000021] g[2.54211998]
>95/100, 1212/1431, d1[0.00000110] d2[0.00000014] g[2.39727831]
>95/100, 1213/1431, d1[0.00000054] d2[0.00000040] g[2.37586737]
>95/100, 1214/1431, d1[0.00000154] d2[0.00000108] g[2.22898388]
>95/100, 1215/1431, d1[0.00000066] d2[0.00000082] g[2.26169920]
>95/100, 1216/1431, d1[0.00000060] d2[0.00000185] g[2.58312130]
>95/100, 1217/1431, d1[0.00000155] d2[0.00000071] g[2.09664702]
>95/100, 1218/1431, d1[0.00000100] d2[0.00000042] g[2.25622392]
>95/100, 1219/1431, d1[0.00001198] d2[0.00000156] g[1.75739563]
>95/100, 1220/1431, d1[0.00000054] d2[0.00000046] g[2.61366725]
>95/100, 1221/1431, d1[0.00000078] d2[0.00000034] g[2.27552032]
>95/100, 1222/1431, d1[0.00000770] d2[0.00000156] g[1.95472705]
>95/100, 1223/1431, d1[0.00000161] d2[0.00000261] g[2.26664948]
>95/100, 1224/1431, d1[0.00000275] d2[0.00000049] g[1.99315834]
>95/100, 1225/1431, d1[0.00000131] d2[0.

>95/100, 1339/1431, d1[0.00000097] d2[0.00000216] g[2.28134489]
>95/100, 1340/1431, d1[0.00000487] d2[0.00000058] g[2.01098132]
>95/100, 1341/1431, d1[0.00000072] d2[0.00000112] g[2.19332743]
>95/100, 1342/1431, d1[0.00000079] d2[0.00000124] g[2.63807487]
>95/100, 1343/1431, d1[0.00000626] d2[0.00000028] g[1.90511179]
>95/100, 1344/1431, d1[0.00000167] d2[0.00000063] g[1.89177573]
>95/100, 1345/1431, d1[0.00000071] d2[0.00000085] g[2.56220126]
>95/100, 1346/1431, d1[0.00000051] d2[0.00000051] g[2.28162479]
>95/100, 1347/1431, d1[0.00000180] d2[0.00000584] g[2.11963940]
>95/100, 1348/1431, d1[0.00000436] d2[0.00000326] g[1.88160908]
>95/100, 1349/1431, d1[0.00000294] d2[0.00000050] g[2.11010981]
>95/100, 1350/1431, d1[0.00000101] d2[0.00000025] g[2.22857165]
>95/100, 1351/1431, d1[0.00000319] d2[0.00000174] g[1.93798256]
>95/100, 1352/1431, d1[0.00000080] d2[0.00000030] g[2.47446084]
>95/100, 1353/1431, d1[0.00000025] d2[0.00000051] g[2.76358247]
>95/100, 1354/1431, d1[0.00000155] d2[0.